<a href="https://colab.research.google.com/github/danyssilva/RNModelos/blob/main/Rede_Neural_Modelos_de_Processos_001.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import zipfile
import os

Extraindo modelos:

In [ ]:
zip_path = "/content/Models.zip"  # Caminho do arquivo ZIP carregado
extract_path = "/content/modelos"  # Local onde os arquivos serão extraídos

with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(extract_path)

print("Arquivos extraídos para modelos:", extract_path)


Arquivos extraídos para modelos: /content/modelos


Extraindo logs de teste:

In [ ]:
zip_path = "/content/Test Logs.zip"  # Caminho do arquivo ZIP carregado
extract_path = "/content/testes"  # Local onde os arquivos serão extraídos

with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(extract_path)

print("Arquivos extraídos para testes:", extract_path)


Arquivos extraídos para testes: /content/testes


Extraindo base de treinamento:

In [ ]:
zip_path = "/content/Training Logs.zip"  # Caminho do arquivo ZIP carregado
extract_path = "/content/treinamento"  # Local onde os arquivos serão extraídos

with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(extract_path)

print("Arquivos extraídos para treinamento:", extract_path)


Arquivos extraídos para treinamento: /content/treinamento


In [ ]:
# --- Instalação de Dependências ---
!pip install pm4py
!pip install scikit-learn
!pip install torch
!pip install bpmn-python

# --- Importação de Bibliotecas ---
import pm4py
import torch
import torch.nn as nn
import torch.optim as optim
from sklearn.preprocessing import StandardScaler
import numpy as np
import os
import time



  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 22.7 MB/s eta 0:00:00
  Created wheel for intervaltree: filename=intervaltree-3.1.0-py2.py3-none-any.whl size=26097 sha256=1ae6644250747d4427aceb07d259a9344570a72a7b507e1fd8dcc5ceb71a928c
  Stored in directory: /root/.cache/pip/wheels/31/d7/d9/eec6891f78cac19a693bd40ecb8365d2f4613318c145ec9816
Successfully built intervaltree
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 2.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 92.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 74.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 43.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 6.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 10.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━

/usr/local/lib/python3.11/dist-packages/cudf/utils/_ptxcompiler.py:64: UserWarning: Error getting driver and runtime versions:

stdout:



stderr:

Traceback (most recent call last):
  File "<string>", line 4, in <module>
  File "/usr/local/lib/python3.11/dist-packages/numba_cuda/numba/cuda/cudadrv/driver.py", line 314, in __getattr__
    raise CudaSupportError("Error at driver init: \n%s:" %
numba.cuda.cudadrv.error.CudaSupportError: Error at driver init: 

CUDA driver library cannot be found.
If you are sure that a CUDA driver is installed,
try setting environment variable NUMBA_CUDA_DRIVER
with the file path of the CUDA driver shared library.
:


Not patching Numba
  warnings.warn(msg, UserWarning)
/usr/local/lib/python3.11/dist-packages/cudf/utils/gpu_utils.py:62: UserWarning: Failed to dlopen libcuda.so.1
  warnings.warn(str(e))


# --- Função para Extrair Restrições SBMN ---


In [ ]:
from pm4py.objects.log.importer.xes import importer as xes_importer

def extrair_restricoes_sbmn(log_path):
    log = xes_importer.apply(log_path)

    atividades = set()
    dependencias = set()
    xor_dependencias = set()
    uniao_dependencias = set()

    for trace in log:
        eventos = [e['concept:name'] for e in trace]
        atividades.update(eventos)

        for i in range(len(eventos) - 1):
            dependencias.add((eventos[i], eventos[i + 1]))

        for i in range(len(eventos)):
            for j in range(i + 1, len(eventos)):
                if eventos[i] != eventos[j]:
                    xor_dependencias.add((eventos[i], eventos[j]))

        uniao_dependencias.update(dependencias.union(xor_dependencias))

    return list(atividades), list(dependencias), list(xor_dependencias), list(uniao_dependencias)


# --- Função para Processar Modelos BPMN ---


In [ ]:
!pip install --upgrade bpmn-python # Upgrade bpmn-python to the latest version
from bpmn_python.bpmn_diagram_rep import BpmnDiagramGraph # Correct the class name

def extrair_estrutura_bpmn(bpmn_path):
    bpmn_graph = BPMNDiagramGraph()
    bpmn_graph.load_diagram_from_file(bpmn_path)

    atividades = set()
    dependencias = set()
    xor_dependencias = set()
    uniao_dependencias = set()

    for node_id, node_type in bpmn_graph.get_nodes():
        if node_type in ["task", "activity"]:
            atividades.add(node_id)

    for source, target in bpmn_graph.get_edges():
        dependencias.add((source, target))

    for atividade1 in atividades:
        for atividade2 in atividades:
            if atividade1 != atividade2:
                xor_dependencias.add((atividade1, atividade2))

    uniao_dependencias.update(dependencias.union(xor_dependencias))

    return list(atividades), list(dependencias), list(xor_dependencias), list(uniao_dependencias)




# --- Função para Gerar Embeddings ---


In [ ]:
def gerar_embedding(atividades, dependencias, xor, uniao):
    embedding = np.zeros(100)
    embedding[0] = len(atividades)
    embedding[1] = len(dependencias)
    embedding[2] = len(xor)
    embedding[3] = len(uniao)
    return embedding



# --- Função para Calcular o Score Harmônico ---


In [ ]:
def calcular_score(metrica1, metrica2, metrica3, metrica4):
    return 4 / ((1 / (metrica1 + 1e-6)) + (1 / (metrica2 + 1e-6)) + (1 / (metrica3 + 1e-6)) + (1 / (metrica4 + 1e-6)))


# --- Modelo de Rede Neural ---


In [ ]:
class ModeloClassificacao(nn.Module):
    def __init__(self, input_size):
        super(ModeloClassificacao, self).__init__()
        self.fc1 = nn.Linear(input_size, 64)
        self.fc2 = nn.Linear(64, 32)
        self.fc3 = nn.Linear(32, 1)

    def forward(self, x):
        x = torch.relu(self.fc1(x))
        x = torch.relu(self.fc2(x))
        x = torch.sigmoid(self.fc3(x))
        return x


# --- Função de Treinamento ---


In [ ]:
def treinar_modelo(X, y):
    X_tensor = torch.tensor(X, dtype=torch.float32)
    y_tensor = torch.tensor(y, dtype=torch.float32).view(-1, 1)

    modelo = ModeloClassificacao(X.shape[1])
    criterio = nn.BCELoss()
    otimizador = optim.Adam(modelo.parameters(), lr=0.001)

    for epoca in range(100):
        saida = modelo(X_tensor)
        perda = criterio(saida, y_tensor)
        otimizador.zero_grad()
        perda.backward()
        otimizador.step()
        if epoca % 10 == 0:
            print(f"Época {epoca}, Perda: {perda.item()}")

    return modelo


# --- Função para Classificação ---


In [ ]:
def classificar_modelos(modelo, embedding1, embedding2):
    entrada = torch.tensor(np.abs(embedding1 - embedding2), dtype=torch.float32)
    saida = modelo(entrada)
    return saida.item()


# --- Função para Processar Diretório de Logs ---


In [ ]:
def processar_logs(diretorio):
    embeddings = []
    arquivos = []

    for arquivo in os.listdir(diretorio):
        if arquivo.endswith(".xes"):
            caminho = os.path.join(diretorio, arquivo)
            print(f"Processando: {arquivo}")
            atividades, dep, xor, uniao = extrair_restricoes_sbmn(caminho)
            embedding = gerar_embedding(atividades, dep, xor, uniao)
            embeddings.append(embedding)
            arquivos.append(arquivo)

    return embeddings, arquivos


# --- Função para Processar Diretório de Modelos BPMN ---


In [ ]:
def processar_modelos(diretorio):
    embeddings = []
    arquivos = []

    for arquivo in os.listdir(diretorio):
        if arquivo.endswith(".bpmn"):
            caminho = os.path.join(diretorio, arquivo)
            print(f"Processando Modelo: {arquivo}")
            atividades, dep, xor, uniao = extrair_estrutura_bpmn(caminho)
            embedding = gerar_embedding(atividades, dep, xor, uniao)
            embeddings.append(embedding)
            arquivos.append(arquivo)

    return embeddings, arquivos


# --- Pipeline Principal ---


In [ ]:
diretorio_logs = "/content/treinamento"

diretorio_modelos = "/content/modelos"

# Extração de Embeddings
start_time = time.time()
embeddings, arquivos = processar_logs(diretorio_logs)
restricoes_tempo = time.time() - start_time
print(f"Tempo para extrair restrições: {restricoes_tempo:.2f} segundos")

# Extração de Embeddings de Modelos BPMN
embeddings_modelos, arquivos_modelos = processar_modelos(diretorio_modelos)

# Simulação de Labels e Treinamento
X = []
y = []

for i in range(len(embeddings)):
    for j in range(len(embeddings_modelos)):
        X.append(np.abs(embeddings[i] - embeddings_modelos[j]))
        y.append(1 if i == j else 0)

X = np.array(X)
y = np.array(y)

modelo = treinar_modelo(X, y)


Processando: pdc2022_0101104.xes


parsing log, completed traces ::   0%|          | 0/1000 [00:00<?, ?it/s]

Processando: pdc2022_0100013.xes


parsing log, completed traces ::   0%|          | 0/1000 [00:00<?, ?it/s]

Processando: pdc2022_1101111.xes


...

parsing log, completed traces ::   0%|          | 0/1000 [00:00<?, ?it/s]

Processando: pdc2022_0101114.xes


parsing log, completed traces ::   0%|          | 0/1000 [00:00<?, ?it/s]

Tempo para extrair restrições: 129.46 segundos


IndexError: tuple index out of range

Testes

In [ ]:
# Defina o diretório de teste
diretorio_teste = "/content/testes"

# Extraia os embeddings dos logs de teste
embeddings_teste, arquivos_teste = processar_logs(diretorio_teste)

# Teste a similaridade entre dois logs de teste
resultado = classificar_modelos(modelo, embeddings_teste[0], embeddings_teste[1])
print(f"Similaridade entre {arquivos_teste[0]} e {arquivos_teste[1]}: {resultado}")

In [ ]:
from google.colab import drive
drive.mount('/content/drive')